In [134]:
import requests
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number
from geopy.geocoders import Nominatim
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from IPython.display import display, HTML
from pyspark.sql import functions as F
from pyspark.sql.functions import percentile_approx
from pyspark.sql.types import StructType, StructField, StringType, DoubleType

After reading the raw JSON file, the file contains customer transactions. Things to note in the raw json file:
1. personal_detail column: Contains a JSON string (not a nested object), with personal attributes of the customer such as person_name, gender, dob, job, and address
2. address field: A JSON string, nested within personal_detail with address details like street, city, state, and zip.

Points 1 and 2 can be observed in the Kaggle link provided: https://www.kaggle.com/datasets/e47f88e5e8ce59c9598475a107d9a80ebc363a83859a59facb069b13a9001773 under the "About this file" section

**Challenge:** Currently pyspark identifies the nested address field in the personal_detail column as a string which does not allow me to directly analyse the information within the column

In [135]:
# Start the Spark session
spark = SparkSession.builder.appName("Paynet_Assessment").getOrCreate()

# Read the raw JSON file into a DataFrame
file_path = r"C:\cc_sample_transaction.json"
df = spark.read.json(file_path)

# limit 100 to process the df more efficiently as the pandas driver is not able to handle too much data
df_inspect = df.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect.to_html(max_rows=100, max_cols=100)}
</div>
"""))

# Solution Breakdown:

**Thought Process Summary:** 
The raw JSON file contained nested fields that were stored as JSON strings inside columns, instead of structured JSON objects. This meant I couldn’t access or analyse them directly using standard DataFrame operations.

**To make the data usable:**

1. I used from_json() along with a custom schema to parse the stringified JSON in the personal_detail column.
2. Although Spark supports schema-on-read, it doesn't apply to nested JSON stored as strings because Spark treats them as plain text and can't infer internal structure automatically.
3. Therefore, I defined schemas for both the personal_detail field and its nested address field before parsing them.
4. After parsing, I flattened the columns to produce a clean DataFrame
5. This structure is better suited for downstream analysis, visualization, or machine learning tasks.

In [136]:
# Step 1: Define schema for the inner 'address' field (which is inside personal_detail)
address_schema = StructType([
    StructField("street", StringType(), True),
    StructField("city", StringType(), True),
    StructField("state", StringType(), True),
    StructField("zip", StringType(), True)
])

# Step 2: Define schema for the 'personal_detail' field, which is a JSON string
# Note: The 'address' here is still a string, which will be parsed next
personal_schema = StructType([
    StructField("person_name", StringType(), True),
    StructField("gender", StringType(), True),
    StructField("address", StringType(), True),  # Still a string
    StructField("lat", StringType(), True),
    StructField("long", StringType(), True),
    StructField("city_pop", StringType(), True),
    StructField("job", StringType(), True),
    StructField("dob", StringType(), True)
])

# Step 3: Parse the 'personal_detail' string column using the defined schema
df = df.withColumn("personal_detail_parsed", from_json(col("personal_detail"), personal_schema))

# Step 4: Parse the 'address' string inside 'personal_detail_parsed'
df = df.withColumn("address_parsed", from_json(col("personal_detail_parsed.address"), address_schema))

# Step 5: Select all necessary columns, including flattened nested fields
# Note: Address was not selected under personal_detail_parsed since information under the address has been flatted as part of the dataframe
df_cleaned = df.select(
    "trans_num",                   # Unique transaction ID
    "amt",                         # Transaction amount
    "category",                    # Category of transaction
    "cc_bic", "cc_num",            # Credit card details
    "merchant", "is_fraud",        # Merchant and fraud indicator
    "merch_lat", "merch_long",     # Merchant geo-coordinates
    "merch_zipcode",               # Merchant ZIP code
    "merch_eff_time",              # Merchant effective timestamp
    "merch_last_update_time",      # Last update time
    "trans_date_trans_time",       # Transaction timestamp
    "personal_detail_parsed.city_pop",  # City population from user profile
    "personal_detail_parsed.lat",       # User latitude
    "personal_detail_parsed.long",      # User longitude
    "personal_detail_parsed.job",       # User occupation
    "personal_detail_parsed.dob",       # Date of birth
    "personal_detail_parsed.gender",    # Gender
    "personal_detail_parsed.person_name",  # Full name string
    "address_parsed.*"                  # Flattened fields: street, city, state, zip
)

df_inspect1 = df_cleaned.limit(10).toPandas()
# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect1.to_html(max_rows=100, max_cols=100)}
</div>
"""))

In [137]:
print(df_cleaned.columns)

['trans_num', 'amt', 'category', 'cc_bic', 'cc_num', 'merchant', 'is_fraud', 'merch_lat', 'merch_long', 'merch_zipcode', 'merch_eff_time', 'merch_last_update_time', 'trans_date_trans_time', 'city_pop', 'lat', 'long', 'job', 'dob', 'gender', 'person_name', 'street', 'city', 'state', 'zip']


In [138]:
df_cleaned.printSchema()

root
 |-- trans_num: string (nullable = true)
 |-- amt: string (nullable = true)
 |-- category: string (nullable = true)
 |-- cc_bic: string (nullable = true)
 |-- cc_num: string (nullable = true)
 |-- merchant: string (nullable = true)
 |-- is_fraud: string (nullable = true)
 |-- merch_lat: string (nullable = true)
 |-- merch_long: string (nullable = true)
 |-- merch_zipcode: string (nullable = true)
 |-- merch_eff_time: string (nullable = true)
 |-- merch_last_update_time: string (nullable = true)
 |-- trans_date_trans_time: string (nullable = true)
 |-- city_pop: string (nullable = true)
 |-- lat: string (nullable = true)
 |-- long: string (nullable = true)
 |-- job: string (nullable = true)
 |-- dob: string (nullable = true)
 |-- gender: string (nullable = true)
 |-- person_name: string (nullable = true)
 |-- street: string (nullable = true)
 |-- city: string (nullable = true)
 |-- state: string (nullable = true)
 |-- zip: string (nullable = true)



Analyse all date columns

In [139]:
df_time = df_cleaned.select("trans_date_trans_time", "merch_last_update_time", "merch_eff_time")
df_inspect2 = df_time.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect2.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Convert **trans_date_trans_time** column into format human-readable timestamp format in UTC +8 timezone (e.g., YYYY-MM-DD HH:MM.SSSSSS Z)

In [140]:
df_time = df_cleaned.withColumn(
    "trans_date_trans_time",
    concat(
        date_format(
            to_timestamp(col("trans_date_trans_time"), "yyyy-MM-dd HH:mm:ss") + expr("INTERVAL 8 HOURS"),
            "yyyy-MM-dd HH:mm.SSSSSS"
        ),
        lit(" +08:00")
    )
)
df_inspect3 = df_time.limit(100).toPandas()
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect3.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Identify the length of Unix Timestamp in both **merch_eff_time** and **merch_eff_time** column

In [141]:
distinct_lengths = df_time.select(
    F.length(F.col("merch_eff_time")).alias("length"),
    F.lit("merch_eff_time").alias("column_name")
).union(
    df_time.select(
        F.length(F.col("merch_last_update_time")).alias("length"),
        F.lit("merch_last_update_time").alias("column_name")
    )
)

df_inspect4 = distinct_lengths.distinct().orderBy("length").limit(100).toPandas()
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect4.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Convert **merch_last_update_time** and **merch_eff_time** column from UNIX timestamp into format human-readable timestamp format in UTC +8 timezone (e.g., YYYY-MM-DD HH:MM.SSSSSS Z)

Unix Length Conversion (Length)
1. 10 digits represent **Seconds** (divide by 1), date: 1970 to ~2286
2. 13 digits represent **Milliseconds** (divide 1000), date: 1970 to 2000s
3. 16 digits represent **Microseconds** (divide 1,000,000), date: 1970s to 2000s
4. 19 digits represent **Nanoseconds** (divide 1,000,000,000), date: 2024+ (modern usage)

In [142]:
# Function to adjust Unix timestamp dynamically based on its length using ranges
# Note: I casted both columns as long as original data type is in string format
def adjust_unix_timestamp(column):
    # Handle different length ranges of Unix timestamps
    return F.when(F.length(column).between(10, 11), column.cast("long")) \
             .when(F.length(column).between(12, 13), (column.cast("long") / 1000)) \
             .when(F.length(column).between(14, 15), (column.cast("long") / 1000000)) \
             .otherwise(column.cast("long") / 1000000000)

# Apply the adjustment dynamically to both columns
df_time_unix = df_time.withColumn("merch_eff_time", adjust_unix_timestamp(F.col("merch_eff_time"))) \
                 .withColumn("merch_last_update_time", adjust_unix_timestamp(F.col("merch_last_update_time")))

# Convert Unix timestamp (seconds) to PySpark timestamp
df_time_unix = df_time_unix.withColumn("merch_eff_time", F.from_unixtime(F.col("merch_eff_time"))) \
                 .withColumn("merch_last_update_time", F.from_unixtime(F.col("merch_last_update_time")))

# Convert timestamps to UTC+8 (Asia/Singapore timezone)
df_time_unix = df_time_unix.withColumn("merch_eff_time", F.from_utc_timestamp(F.col("merch_eff_time"), "Asia/Singapore")) \
                 .withColumn("merch_last_update_time", F.from_utc_timestamp(F.col("merch_last_update_time"), "Asia/Singapore"))

# Format the timestamps to the desired string format (YYYY-MM-DD HH:MM.SSSSSS Z)
df_time_unix = df_time_unix.withColumn("merch_eff_time", F.date_format(F.col("merch_eff_time"), "yyyy-MM-dd HH:mm:ss.SSSSSS Z")) \
                 .withColumn("merch_last_update_time", F.date_format(F.col("merch_last_update_time"), "yyyy-MM-dd HH:mm:ss.SSSSSS Z"))

df_inspect5 = df_time_unix.limit(100).toPandas()
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect5.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Analyze person_name column for cleaning

In [143]:
df_name = df_time_unix.select("person_name")

# Convert to Pandas (limit 100 rows)
df_inspect6 = df_name.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect6.to_html(max_rows=1000, max_cols=100)}
</div>
"""))

After analysing the person_name column, I noticed that
1. There are alot of symbols among each name record
2. Irrelevant names tend to come after the surename (e.g. NOOOOO, eeeee)

Now I want to check the maximum number of parts within each name

**Steps Needed:**
1. Replace all symbols as spaces
2. Remove all unnecessary spaces as well as leading and trailing whitespaces
3. Remove last section of the name (irrelevant names)

In [144]:
df_name_check = df_name.withColumn(
    "person_name",
    trim(  # Remove leading/trailing spaces
        regexp_replace(  # Replace multiple spaces with a single space
            regexp_replace(col("person_name"), r"[^a-zA-Z0-9]", " "),  # Replace symbols with space
            r"\s+", " "  # Replace multiple spaces with a single space
        )
    )
)

df_name_check = df_name_check \
    .withColumn("person_name_comma", regexp_replace(col("person_name"), r" ", ",")) \
    .withColumn("name_sections", size(split(col("person_name_comma"), ",")))

df_inspect8 = df_name_check.select("person_name_comma", "person_name", "name_sections").orderBy(col("name_sections").desc()).limit(10).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect8.to_html(max_rows=100, max_cols=100)}
</div>
"""))

**Last Step:**
1. Remove last part of the name

In [145]:
df_name_trimmed = df_name_check.withColumn(
    "person_name",
    when(
        col("name_sections") == 3,
        concat_ws(" ", split(col("person_name"), " ").getItem(0), split(col("person_name"), " ").getItem(1))
    ).otherwise(col("person_name"))
)

df_inspect9 = df_name_trimmed.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect9.to_html(max_rows=100, max_cols=100)}
</div>
"""))


Combine code into main dataframe

<i>Note: The cells above used to analyse the person name column is purely to display thought process and is not based on best practice to occupy that much cells</i>

In [146]:
df_name_trim = df_time_unix.withColumn(
    "person_name",
    trim(  # Remove leading/trailing spaces
        regexp_replace(  # Replace multiple spaces with a single space
            regexp_replace(col("person_name"), r"[^a-zA-Z0-9]", " "),  # Replace symbols with space
            r"\s+", " "  # Replace multiple spaces with a single space
        )
    )
)

df_name_trim = df_name_trim \
    .withColumn("person_name_comma", regexp_replace(col("person_name"), r" ", ",")) \
    .withColumn("name_sections", size(split(col("person_name_comma"), ",")))

df_name_trim = df_name_trim.withColumn(
    "person_name",
    when(
        col("name_sections") == 3,
        concat_ws(" ", split(col("person_name"), " ").getItem(0), split(col("person_name"), " ").getItem(1))
    ).otherwise(col("person_name"))
)

# Create columns first and last name from person_name
df_name_split = df_name_trim.withColumn("first_name", split(col("person_name"), " ").getItem(0)) \
                               .withColumn("last_name", split(col("person_name"), " ").getItem(1))

df_name_split= df_name_split.drop("person_name_comma", "name_sections", "person_name")

df_inspect10 = df_name_split.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect10.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Now that I have completed what was directly stated in the assessment, I will now clean and reorder the dataframe to provide more meaningful information.

**Thought process on reordering the columns:**

Considering that this dataset constain credit card transactions and can be analysed for fraud detection and behaviour analysis, the first few columns should tell me **WHO, WHAT, WHERE, AND WHEN** so that i can spot issues, patterns and anamalies quickly. The columns are ordered by groupings.

1. **Transaction insights (WHAT, WHEN, WHO):** "trans_date_trans_time", "amt", "category", "is_fraud", "merchant" which gives the transaction context
2. **Customer Identity:** "first_name", "last_name", "gender", "dob", "job" which helps me identify who made the transaction
3. **Transaction ID and Card Information:** "trans_num", "cc_num", "cc_bic"
4. **Merchant Info (WHERE the transaction happened):** "merchant", "merch_lat", "merch_long", "merch_zipcode", "merch_eff_time", "merch_last_update_time" which helps me understand the merchants behaviour, geography and if the merchant makes sense for the user
5. **Customer Location:** "street", "city", "state", "zip", "lat", "long", "city_pop" which helps me compare the merchant and the customers geography

In [147]:
# Convert data in the datframe to uppercase, convert all string = NONE, NA, NULL, blanks to null
for c in df_name_split.columns:
    if df_name_split.schema[c].dataType == StringType():
        df_name_split = df_name_split.withColumn(
            c,
            when(
                upper(col(c)).isin("NONE", "NA", "NULL", ""), 
                lit(None)
            ).otherwise(upper(col(c)))
        )

ordered_columns = [
    "trans_date_trans_time", "amt", "category", "is_fraud", "merchant",
    "first_name", "last_name", "gender", "dob", "job",
    "trans_num", "cc_num", "cc_bic",
    "merch_lat", "merch_long", "merch_zipcode", "merch_eff_time", "merch_last_update_time",
    "street", "city", "state", "zip", "lat", "long", "city_pop"
]

# Reorder DataFrame
df_reordered = df_name_split.select(*ordered_columns)

df_inspect11 = df_reordered.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect11.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Create two new columns from **trans_date_trans_time** named trans_date, trans_time with formats yyyy-mm-dd and HH:MM respectively to separate the date and time of transactions

In [148]:
df_reordered = df_reordered.withColumn("trans_date", split(col("trans_date_trans_time"), " ")[0])
df_reordered = df_reordered.withColumn("trans_time (24h)", split(col("trans_date_trans_time"), " ")[1].substr(1, 5))
df_reordered = df_reordered.drop("trans_date_trans_time")
df_inspect12 = df_reordered.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect12.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Create a new column **age** from yyyy in dob to identify the age of the customer

In [149]:
df_age = df_reordered.withColumn("age", year(current_date()) - year(to_date(col("dob"), "yyyy-MM-dd")))

df_inspect13 = df_age.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect13.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Import US Zip code dataset with assumption that the merchants are in the US to identify the merchant's state but could not identify all states after joining both dataframes together. Main purpose was in hopes to identify unsual transaction between user and merchant

<i>Note: I tried getting zip code worldwide dataset from kaggle but could not find available datasets</i>

In [150]:
file_path = r"C:\US_Zip_Code.csv"

# Read the CSV file
df_zip = spark.read.option("header", True).csv(file_path)
df_zip = df_zip.toDF(*[f"us_{col.lower()}" for col in df_zip.columns])
df_inspect14 = df_zip.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect14.to_html(max_rows=100, max_cols=100)}
</div>
"""))

In [151]:
df_age_alias = df_age.alias("age")
df_zip_alias = df_zip.alias("zip")

# Perform the join
df_joined = df_age_alias.join(
    df_zip_alias,
    col("zip.us_zip") == col("age.merch_zipcode"),
    how="left"
)

# Rename the 'prefix_us_state' column to 'merch_state'
df_merch_state = df_joined.withColumnRenamed("us_state", "merch_state")

df_merch_state = df_merch_state.select("age.*", "merch_state")

window_spec = Window.partitionBy("trans_num", "first_name", "last_name", "trans_date", "trans_time (24h)") \
                    .orderBy("trans_date")  # or any other column to keep the latest/earliest

# Assign row numbers
df_merch_state = df_merch_state.withColumn("row_num", row_number().over(window_spec))

# Filter to keep only the first row in each group
df_merch_state = df_merch_state.filter("row_num = 1").drop("row_num")

df_inspect15 = df_merch_state.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect15.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Create a new column named **trans_day** that can help in visualising the days with high transactions

In [152]:
df_trans_day = df_merch_state.withColumn(
    "trans_day",
    date_format(to_date("trans_date", "yyyy-MM-dd"), "EEEE")
)

df_inspect16 = df_trans_day.limit(1000).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect16.to_html(max_rows=1000, max_cols=100)}
</div>
"""))

Create a new column named **time_of_day** to categorize the time of day of transaction made. Could also help to identify frequent fraudulant activity upon data analysis

In [153]:
df_trans_hour = df_trans_day.withColumn("trans_hour", substring("trans_time (24h)", 1, 2).cast("int"))
df_time_day = df_trans_hour.withColumn(
    "time_of_day",
    when((col("trans_hour") >= 0) & (col("trans_hour") < 6), "Night")
    .when((col("trans_hour") >= 6) & (col("trans_hour") < 12), "Morning")
    .when((col("trans_hour") >= 12) & (col("trans_hour") < 18), "Afternoon")
    .otherwise("Evening")
).drop("trans_hour")

df_inspect17 = df_time_day.limit(1000).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect17.to_html(max_rows=1000, max_cols=100)}
</div>
"""))

Create a new column named **age_group** to categorize ages into bins. This column could potentially help in visualising the fraud cases by age groups to identify ages prone to credit card fraud

In [154]:
df_age_group = df_time_day.withColumn(
    "age_group",
    when(col("age") <= 19, "19 and Under")
    .when((col("age") >= 20) & (col("age") <= 29), "20 to 29")
    .when((col("age") >= 30) & (col("age") <= 39), "30 to 39")
    .when((col("age") >= 40) & (col("age") <= 49), "40 to 49")
    .when((col("age") >= 50) & (col("age") <= 59), "50 to 59")
    .when((col("age") >= 60) & (col("age") <= 69), "60 to 69")
    .when((col("age") >= 70) & (col("age") <= 79), "70 to 79")
    .otherwise("80 and Over")
)

df_inspect18 = df_age_group.limit(1000).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect18.to_html(max_rows=1000, max_cols=100)}
</div>
"""))

Update state column to display full name instead of state abbreviation

In [155]:
file_path = r"C:\US_State.csv"

# Read the CSV file
df_us_state = spark.read.option("header", True).csv(file_path)
df_us_state = df_us_state.toDF(*[f"us_{col.lower()}" for col in df_us_state.columns])

df_age_alias = df_age_group.alias("age")
df_state_alias = df_us_state.alias("state")

# Perform the join and drop state column
df_joined = df_age_alias.join(
    df_state_alias,
    col("state.us_state_po") == col("age.state"),
    how="left"
).drop("state")

# Rename the 'us_state' column to 'state'
df_cust_state = df_joined.withColumnRenamed("us_state", "state")

df_cust_state = df_cust_state.select("age.*", "state")

window_spec = Window.partitionBy("trans_num", "first_name", "last_name", "trans_date", "trans_time (24h)") \
                    .orderBy("trans_date")  # or any other column to keep the latest/earliest

# Assign row numbers
df_cust_state = df_cust_state.withColumn("row_num", row_number().over(window_spec))

# Filter to keep only the first row in each group
df_cust_state = df_cust_state.filter("row_num = 1").drop("row_num")

df_inspect99 = df_cust_state.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect99.to_html(max_rows=100, max_cols=100)}
</div>
"""))

In [156]:
ordered_columns = [
    "trans_date", "trans_time (24h)", "trans_day", "time_of_day", "amt", "category", "is_fraud", "merchant",
    "first_name", "last_name", "gender", "age", "age_group", "dob", "job",
    "trans_num", "cc_num", "cc_bic",
    "merch_lat", "merch_long", "merch_zipcode", "merch_state", "merch_eff_time", "merch_last_update_time",
    "street", "city", "state", "zip", "lat", "long", "city_pop"
]

# Reorder DataFrame
df_reorder = df_cust_state.select(*ordered_columns)

df_inspect19 = df_reorder.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect19.to_html(max_rows=100, max_cols=100)}
</div>
"""))


In [157]:
# Drop duplicates,define window spec
window_spec = Window.partitionBy("trans_num", "first_name", "last_name", "trans_date", "trans_time (24h)") \
                    .orderBy("trans_date")

# Assign row numbers
df_ranked = df_reorder.withColumn("row_num", row_number().over(window_spec))

# Filter to keep only the first row in each group
df_final = df_ranked.filter("row_num = 1").drop("row_num")

df_inspect100 = df_final.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect100.to_html(max_rows=100, max_cols=100)}
</div>
"""))

In [158]:
df_final.printSchema()

root
 |-- trans_date: string (nullable = true)
 |-- trans_time (24h): string (nullable = true)
 |-- trans_day: string (nullable = true)
 |-- time_of_day: string (nullable = false)
 |-- amt: string (nullable = true)
 |-- category: string (nullable = true)
 |-- is_fraud: string (nullable = true)
 |-- merchant: string (nullable = true)
 |-- first_name: string (nullable = true)
 |-- last_name: string (nullable = true)
 |-- gender: string (nullable = true)
 |-- age: integer (nullable = true)
 |-- age_group: string (nullable = false)
 |-- dob: string (nullable = true)
 |-- job: string (nullable = true)
 |-- trans_num: string (nullable = true)
 |-- cc_num: string (nullable = true)
 |-- cc_bic: string (nullable = true)
 |-- merch_lat: string (nullable = true)
 |-- merch_long: string (nullable = true)
 |-- merch_zipcode: string (nullable = true)
 |-- merch_state: string (nullable = true)
 |-- merch_eff_time: string (nullable = true)
 |-- merch_last_update_time: string (nullable = true)
 |-- str

# Analysis

Analysing and understanding transactions where column is_fraud was flagged as 1 

Step 1: Filter fraudulant Transactions

In [159]:
df_fraud = df_final.filter(df_final['is_fraud'] == 1)

df_inspect20 = df_fraud.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect20.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 2: Identify Frequent Fraud Victims

In [160]:
fraud_counts = df_fraud.groupBy("first_name", "last_name").agg(count("*").alias("fraud_count"))
frequent_fraudsters = fraud_counts.filter("fraud_count > 1").orderBy("fraud_count", ascending=False)

df_inspect21 = frequent_fraudsters.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect21.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 3: Analyze Spending Behavior of Fraudulent Users

In [161]:
df_fraud = df_fraud.withColumn("amt", col("amt").cast("double"))

# Now perform the fraud spending aggregation
fraud_spending = df_fraud.groupBy("first_name", "last_name").agg(
    count("*").alias("num_trans"),
    avg("amt").alias("avg_amt"),
    min("amt").alias("min_amt"),
    max("amt").alias("max_amt"),
    sum("amt").alias("total_amt")
)

df_inspect22 = fraud_spending.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect22.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 4: Identify Most Common Fraudulent Merchant (Merchants with high fraud count could be compromised)

In [162]:
fraud_merchants = df_fraud.groupBy("merchant").agg(count("*").alias("fraud_trans_count"))
top_fraud_merchants = fraud_merchants.orderBy("fraud_trans_count", ascending=False)

df_inspect23 = top_fraud_merchants.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect23.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 5: Understanding Time-Based Fraud Patterns

In [163]:
fraud_by_time = df_fraud.groupBy("time_of_day").agg(count("*").alias("fraud_trans_count"))

df_inspect24 = fraud_by_time.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:200px; overflow:auto; border:1px solid lightgray">
    {df_inspect24.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 6: Demographic Fraud Breakdown

In [164]:
# Get distinct age groups and assign an index
age_group_order = df_fraud.select("age_group").distinct().withColumn(
    "age_group_order",
    row_number().over(Window.orderBy("age_group"))
)

# Aggregate fraud count
fraud_demo = df_fraud.groupBy("age_group", "gender").agg(
    count("*").alias("fraud_trans_count")
)

# Join with age group order
fraud_demo = fraud_demo.join(age_group_order, on="age_group", how="left")

# Order by age_group_order and gender
fraud_demo = fraud_demo.orderBy("age_group_order", "gender")

# Drop the helper column
fraud_demo = fraud_demo.drop("age_group_order")

df_inspect25 = fraud_demo.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect25.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 7: Identify Top States with Fraud

In [165]:
fraud_states = df_fraud.groupBy("state").agg(count("*").alias("fraud_trans_count")).orderBy("fraud_trans_count", ascending=False)

df_inspect26 = fraud_states.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect26.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 8: Identify High-Value Fraud Transactions

In [166]:
high_value_fraud = df_fraud.filter(col("amt") > 1000).orderBy("amt", ascending=False)

df_inspect27 = high_value_fraud.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect27.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 9: Identify Fraud Analysis by Transaction Category: Frequency, Rate, and Amount Trends

In [167]:
# Step 1: Calculate total and fraud transaction counts per category
df_txn_rate = df_final.groupBy("category").agg(
    count("*").alias("total_trans"),
    count(when(col("is_fraud") == 1, True)).alias("fraud_trans")
).withColumn(
    "fraud_rate", round(col("fraud_trans") / col("total_trans"), 4)
)

# Step 2: Compute fraud-specific stats
df_fraud_stats = df_fraud.groupBy("category").agg(
    count("*").alias("fraud_tran_count"),
    round(avg(col("amt").cast("double")), 2).alias("avg_fraud_amt")
)

# Step 3: Combine both into a single summary
df_category_summary = df_txn_rate.join(df_fraud_stats, on="category", how="left") \
    .orderBy(col("fraud_tran_count").desc_nulls_last())

df_inspect28 = df_category_summary.drop("fraud_tran_count").limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect28.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Step 10: Compare Fraud vs Normal for a Specific User (In this example we use SCOTT MARTIN as he was identified as the top fraud victim based on the Frequent Fraud Victims List generated above

In [168]:
user_transactions = df_final.filter((col("first_name") == "SCOTT") & (col("last_name") == "MARTIN"))

user_stats = user_transactions.groupBy("is_fraud").agg(
    count("*").alias("num_trans"),
    avg("amt").alias("avg_amt"),
    sum("amt").alias("total_amt")
)

df_inspect29 = user_stats.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:100px; overflow:auto; border:1px solid lightgray">
    {df_inspect29.to_html(max_rows=100, max_cols=100)}
</div>
"""))

# Outlier Detection

Outlier Detection Based on Amount (IQR Method)

Simple EDA has been completed above based on cleaned data. Now i will be attempting to identify fraud and potential fraudulant transactions using the IQR Method based on the amount column in df_final

In [169]:
df_final = df_final.withColumn("amt", col("amt").cast(DoubleType()))

# Calculate Q1 (25th percentile) and Q3 (75th percentile) using approxQuantile
q1 = df_final.approxQuantile("amt", [0.25], 0.05)[0]
q3 = df_final.approxQuantile("amt", [0.75], 0.05)[0]
iqr = q3 - q1

# Define the upper bound for outliers
outlier_upper_bound = q3 + 1.5 * iqr

# Filter transactions that are above the upper bound (outliers)
df_outliers = df_final.filter(col("amt") > outlier_upper_bound)

# Compute average amount per user to compare with the outlier amount
df_user_avg = df_final.groupBy("first_name", "last_name").agg(avg("amt").alias("avg_amt"))

# Join outliers with user average amount to assess how much higher the transaction is
df_outliers = df_outliers.join(df_user_avg, on=["first_name", "last_name"], how="left")

df_outliers = df_outliers.select(
    "first_name", "last_name", "amt", round("avg_amt", 2).alias("avg_amt"),
    "trans_date", "category", "merchant", "is_fraud", "age_group"
).orderBy("first_name", "last_name", "trans_date")

df_inspect30 = df_outliers.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect30.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Based on the list above, I considered narrowing the list down by cross checking the column category with categories with high fraudulant activity (EDA Step 9) to only focus on transactions that falls under the "flagged" categories, however the fraud rate is considered low based on the analysis done. Hence I did not continue narrowing the list down, however it is something that can be done. 

Now that we have the list of fraudulant transactions and potential fraudulant transactions, I will be attempting to generate a list identifying users who were repeatedly targeted and whose transactions were unusually large 

In [170]:
# This step identifies victims who were frequently targeted (3 or more fraud transactions)
# and had high transaction amounts (outliers). These individuals may be more vulnerable to fraud.

# Find victims involved in 3 or more fraud transactions
high_freq_users = df_fraud.groupBy("first_name", "last_name") \
    .count().filter("count >= 3").withColumnRenamed("count", "trans_count")

# Join frequent victims with high-amount outliers to flag strong fraud signals
combined_flags = df_outliers.join(high_freq_users, on=["first_name", "last_name"], how="inner")

# Show victims who were targeted often and for high amounts
df_targeted = combined_flags.select("first_name", "last_name", "amt", "avg_amt", "trans_date", "is_fraud", "category", "merchant", "age_group").orderBy("first_name", "last_name", "trans_date")
df_inspect31 = df_targeted.limit(100).toPandas()

# Display with scrollable HTML box in Jupyter Notebook
display(HTML(f"""
<div style="height:400px; overflow:auto; border:1px solid lightgray">
    {df_inspect31.to_html(max_rows=100, max_cols=100)}
</div>
"""))

Many more exciting insights could be derived from this dataset, however I will conclude here. 